# Tracé des Heat-Maps

Dans ce fichier, nous traçons les cartes de températures illustrant la fréquence des accidents de la route en france en 2019. Pour un souci de clareté les zooms sont effectués sur la France métropolitaine, mais les cartes étant interractives, il est tout à fait possible de se déplacer afin d'explorer d'autre zones. 

In [173]:
%run "/Users/camille/Documents/GitHub/Accidents-corporels/Ouverture_donnees.ipynb"

/Users/camille/Documents/GitHub/Accidents-corporels/Ouverture_donnees.ipynb:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  "source": [


In [174]:
import seaborn as sns
import numpy as np
import folium
from folium import plugins
import pandas as pd
import matplotlib.pyplot as plt

In [175]:
#help(sns.heatmap)
#help(folium.CircleMarker)
#help(plugins.HeatMap)

### Préparation des données 

On récupère ici les coordonnées gps de chaque accident, on les mets au bon format : 
- tableau de float de dimension (n,2) avec n le nombre total d'accidents

In [176]:
#Tous les accidents
df1=df_carac[['lat','long']].astype(str)
df1 = df1.apply(lambda x: x.str.replace(',','.'))
df1=df1.astype(float)
loc_tout_accidents=df1.to_numpy()
#Les accidents graves
df3=df[df['gravite']==2].groupby("Num_Acc")[['lat','long']].aggregate(max)
df3=df3[['lat','long']].astype(str)
df3 = df3.apply(lambda x: x.str.replace(',','.'))
df3=df3.astype(float)
loc_accidents_graves=df3.to_numpy()
#Les accidents peu graves
df4=df[df['gravite']==1].groupby("Num_Acc")[['lat','long']].aggregate(max)
df4=df4[['lat','long']].astype(str)
df4 = df4.apply(lambda x: x.str.replace(',','.'))
df4=df4.astype(float)
loc_accidents_peu_graves=df4.to_numpy()

# pour la différenciation par couleurs
df2=df[['Num_Acc','gravite']].groupby(['Num_Acc']).max()
grav=np.array(df2['gravite'])

## Carte de France métropolitaine

### Localisation des accidents

Dans un premier temps on s'intéresse à la France métropolitaine, on va donc initialiser la carte en la centrant sur Bourges qui se situe environ au centre.

In [177]:
m = folium.Map([47.081012,2.398782], zoom_start=6) #France
#m

On trace ici tous les accidents en représentant chacun d'entre eux par un point bleu 

In [178]:
m = folium.Map([47.081012,2.398782], zoom_start=6) #France
# mark each crash as a point
for index, row in df1.iterrows():
    folium.CircleMarker([row['lat'], row['long']],
                        radius=0.01,
                        #popup=row['name'],
                        #fill_color="#3db7e4", # divvy color
                       ).add_to(m)
    
#m

On différencie maintenant par couleur en fonction de la gravité de l'accident :
- points rouges : accidents graves (ie au moins un blessé hospitalisé ou au moins un tué)
- points verts : accidents peu graves (ie uniquement des blessés légers ou des indemnes)

En zoomant un peu sur Paris par exemple, on observe que hors aglomération les accidents ont l'aire plus grave (surtout des points rouges) qu'en agglomération (surtout des points verts) c'est ce que nous allons chercher à vérifier avec les cartes de température. 

In [179]:
m = folium.Map([47.081012,2.398782], zoom_start=6) #France
# mark each crash as a point : green for low gravity, red for high gravity
for index, row in df1.iterrows():
    col="#4ee43d"
    if (grav[index]==2):
        col="#e4593d" #Rouge si c'est grave
    folium.CircleMarker([row['lat'], row['long']],
                        radius=0.01,
                        #popup=row['name'],
                        color=col
                       ).add_to(m)
    
#m

### Cartes de température

#### Tout type d'accident confondus

In [180]:
m = folium.Map([47.081012,2.398782], zoom_start=6) #France

# plot heatmap
m.add_child(plugins.HeatMap(loc_tout_accidents, radius=12, overlay=False))
#m

On peut faire plusieurs observations sur cette carte de température de la France métropolitaire : 
- Tout d'abbord on constate que le point le plus chaud se situe à Paris. C'est donc à paris qu'il y a le plus d'accidents ce qui parrait logique au vu de la densité de population. 
- On observe ensuite différents points chauds surtout situé au niveau de grandes villes telles que Clermont-Ferrand, Bordeaux ou encore Reims. Cette observation semble cohérente avec la remarque précédente. 
- On peut voir se dessiner certains axes routiers importants comme l'A77 qui relie Paris à Clermont-Ferrand ou l'A9 entre Nîmes et Carcassonne par exemple. Cela semble cohérent avec le fait que les grands axes routiers sont particulièrement fréquentés on peut donc présumer que le risque d'accident est plus élevé.
- Enfin en zoomant sur les points les plus froids on constate qu'il s'agit de zones peu urbanisées et donc peu fréquentées en terme de circulations comme des réserves naturelles 

In [181]:
m = folium.Map([48.856614,2.3522219], zoom_start=12.5) #Paris
#m

# plot heatmap
m.add_child(plugins.HeatMap(loc_tout_accidents, radius=11, name="test", overlay=True))
#m

En zoomant sur la ville de Paris, on constate que le point le plus chaud n'est autre que la fameuse place de l'étoile, connue pour sa quasi anarchie en terme de respect des priorités. On peut également voir deux points chauds au niveau de la concorde et de la place de la répulique, ce sont toutes trois des grandes places parisennes avec beaucoup de trafique c'est résultats ne sont donc pas surprenants 

#### Accidents graves

In [182]:
m = folium.Map([47.081012,2.398782], zoom_start=6) #France

# plot heatmap
m.add_child(plugins.HeatMap(loc_accidents_graves, radius=12, overlay=False))
#m

In [183]:
m = folium.Map([48.856614,2.3522219], zoom_start=12.5) #Paris
#m

# plot heatmap
m.add_child(plugins.HeatMap(loc_accidents_graves, radius=11, name="test", overlay=True))
#m

#### Accidents peu graves

In [184]:
m = folium.Map([47.081012,2.398782], zoom_start=6) #France

# plot heatmap
m.add_child(plugins.HeatMap(loc_accidents_peu_graves, radius=12, overlay=False))
#m

In [185]:
m = folium.Map([48.856614,2.3522219], zoom_start=12.5) #Paris
#m

# plot heatmap
m.add_child(plugins.HeatMap(loc_accidents_peu_graves, radius=11, name="test", overlay=True))
#m